In [1]:
import csv
import itertools
import operator
import numpy as np
import nltk
import sys
from datetime import datetime
from utils import *

import matplotlib.pyplot as plt
%matplotlib inline

In [2]:
nltk.download("book")

[nltk_data] Downloading collection u'book'
[nltk_data]    | 
[nltk_data]    | Downloading package abc to
[nltk_data]    |     /home/jameschien/nltk_data...
[nltk_data]    |   Package abc is already up-to-date!
[nltk_data]    | Downloading package brown to
[nltk_data]    |     /home/jameschien/nltk_data...
[nltk_data]    |   Package brown is already up-to-date!
[nltk_data]    | Downloading package chat80 to
[nltk_data]    |     /home/jameschien/nltk_data...
[nltk_data]    |   Package chat80 is already up-to-date!
[nltk_data]    | Downloading package cmudict to
[nltk_data]    |     /home/jameschien/nltk_data...
[nltk_data]    |   Package cmudict is already up-to-date!
[nltk_data]    | Downloading package conll2000 to
[nltk_data]    |     /home/jameschien/nltk_data...
[nltk_data]    |   Package conll2000 is already up-to-date!
[nltk_data]    | Downloading package conll2002 to
[nltk_data]    |     /home/jameschien/nltk_data...
[nltk_data]    |   Package conll2002 is already up-to-date!
[nl

True

In [3]:
vocabulary_size = 8000
unknown_token = "UNKNOWN_TOKEN"
sentence_start_token = "SENTENCE_START"
sentence_end_token = "SENTENCE_END"

print "Reading CSV file..."
with open('data/reddit-comments-2015-08.csv', 'rb') as f:
    reader = csv.reader(f, skipinitialspace=True)
    reader.next()
    # split full comments into sentence
    sentences = itertools.chain(*[nltk.sent_tokenize(x[0].decode('utf-8').lower()) for x in reader])
    # Append SENTENCE_START and SENTENCE_END
    sentences = ["%s %s %s" % (sentence_start_token, x, sentence_end_token) for x in sentences]
print "Parsed %d sentences." %  (len(sentences))

Reading CSV file...
Parsed 79170 sentences.


In [4]:
# tokenize
tokenized_sentences = [nltk.word_tokenize(sent) for sent in sentences]

# count the word frequencies
word_freq = nltk.FreqDist(itertools.chain(*tokenized_sentences))

# find most common words
vocab = word_freq.most_common(vocabulary_size-1)

# build index_to_word, word_to_index vectors
index_to_word = [x[0] for x in vocab]
index_to_word.append(unknown_token)

word_to_index = dict([(w, i) for i, w in enumerate(index_to_word)])
print "Using vocabulary size %d." % vocabulary_size
print "The least frequent word in our vocabulary is '%s' and appeared %d times." % (vocab[-1][0], vocab[-1][1])

# Replace all words not in out vocabulary with the unknown token
for i, sent in enumerate(tokenized_sentences):
    tokenized_sentences[i] = [w if w in word_to_index else unknown_token for w in sent]

print "\nExample sentence: '%s'" % sentences[0]
print "\nExample sentence after Pre-processing: '%s'" % tokenized_sentences[0]

Using vocabulary size 8000.
The least frequent word in our vocabulary is 'traction' and appeared 10 times.

Example sentence: 'SENTENCE_START i joined a new league this year and they have different scoring rules than i'm used to. SENTENCE_END'

Example sentence after Pre-processing: '[u'SENTENCE_START', u'i', u'joined', u'a', u'new', u'league', u'this', u'year', u'and', u'they', u'have', u'different', u'scoring', u'rules', u'than', u'i', u"'m", u'used', u'to', u'.', u'SENTENCE_END']'


In [5]:
# Create the training data
X_train = np.asarray([[word_to_index[w] for w in sent[:-1]] for sent in tokenized_sentences])
y_train = np.asarray([[word_to_index[w] for w in sent[1:]] for sent in tokenized_sentences])

In [6]:
# Print an training data example
x_example, y_example = X_train[17], y_train[17]
print "x:\n%s\n%s" % (" ".join([index_to_word[x] for x in x_example]), x_example)
print "\ny:\n%s\n%s" % (" ".join([index_to_word[y] for y in y_example]), y_example)

x:
SENTENCE_START what are n't you understanding about this ? !
[0, 51, 27, 16, 10, 861, 54, 25, 34, 69]

y:
what are n't you understanding about this ? ! SENTENCE_END
[51, 27, 16, 10, 861, 54, 25, 34, 69, 1]


In [7]:
class RNNNumpy:
    
    def __init__(self, word_dim, hidden_dim=100, bptt_truncate=4):
        self.word_dim = word_dim
        self.hidden_dim = hidden_dim
        self.bptt_truncate = bptt_truncate
        # randomly initialize the network parameters
        self.U = np.random.uniform(-np.sqrt(1./word_dim), np.sqrt(1./word_dim), (hidden_dim, word_dim))
        self.V = np.random.uniform(-np.sqrt(1./hidden_dim), np.sqrt(1./hidden_dim), (word_dim, hidden_dim))
        self.W = np.random.uniform(-np.sqrt(1./hidden_dim), np.sqrt(1./hidden_dim), (hidden_dim, hidden_dim))
        

In [8]:
def forward_propagation(self, x):
    # total number of time steps
    T = len(x)
    # During forward propagation we save all hidden states in s
    # we add one additional element for initial hidden, which we set to 0
    s = np.zeros((T + 1, self.hidden_dim))
    s[-1] = np.zeros(self.hidden_dim)
    # The outputs at each time step.
    o = np.zeros((T, self.word_dim))
    for t in np.arange(T):
        # Note that we are indexing U by x[t].
        # This is the same as multiplying U with a one-hot vector
        s[t] = np.tanh(self.U[:,x[t]] + self.W.dot(s[t-1]))
        o[t] = np.exp(self.V.dot(s[t])) / np.sum(np.exp(self.V.dot(s[t])), axis=0)
    return [o, s]
RNNNumpy.forward_propagation = forward_propagation

In [9]:
def predict(self, x):
    # perform forward propagation and return index of the highest score
    o, s = self.forward_propagation(x)
    return np.argmax(o, axis=1)
RNNNumpy.predict = predict

In [10]:
np.random.seed(10)
model = RNNNumpy(vocabulary_size)
o, s = model.forward_propagation(X_train[10])
print o.shape
print o

(45, 8000)
[[ 0.00012408  0.0001244   0.00012603 ...,  0.00012515  0.00012488
   0.00012508]
 [ 0.00012536  0.00012582  0.00012436 ...,  0.00012482  0.00012456
   0.00012451]
 [ 0.00012387  0.0001252   0.00012474 ...,  0.00012559  0.00012588
   0.00012551]
 ..., 
 [ 0.00012406  0.00012463  0.00012539 ...,  0.00012617  0.00012463
   0.00012589]
 [ 0.00012547  0.00012431  0.00012485 ...,  0.00012427  0.00012611
   0.00012472]
 [ 0.00012482  0.00012529  0.00012477 ...,  0.00012488  0.00012508
   0.0001267 ]]


In [11]:
predictions = model.predict(X_train[10])
print predictions.shape
print predictions

(45,)
[1284 5221 7653 7430 1013 3562 7366 1627 7290 3251 7299 6722  565  238 2539
   21 6548  261 5274 2082 1835 5376 3522  477 7051 7352 7715 3822 6914 5059
 3850 6176  743 2082 5561 2182 6569 2800 2752 6821 4437 7021 6399 6912 3922]


In [12]:
def calculate_total_loss(self, x, y):
    L = 0
    for i in np.arange(len(y)):
        o, s = self.forward_propagation(x[i])
        # We only care about prediction of the "correct" words
        correct_word_predictions = o[np.arange(len(y[i])), y[i]]
        # Add to the loss based on how off we were
        L += -1 * np.sum(np.log(correct_word_predictions))
    return L

def calculate_loss(self, x, y):
    # Divide the total loss by the number of training examples
    N = np.sum((len(y_i) for y_i in y))
    return self.calculate_total_loss(x, y)/N

RNNNumpy.calculate_total_loss = calculate_total_loss
RNNNumpy.calculate_loss = calculate_loss

In [13]:
# Limit to 1000 examples to save time
print "Expected Loss for random predictions: %f" % np.log(vocabulary_size)
print "Actual loss: %f" % model.calculate_loss(X_train[:1000], y_train[:1000])

Expected Loss for random predictions: 8.987197
Actual loss: 8.987430


In [14]:
def bptt(self, x, y):
    T = len(y)
    # Perform forward propagation
    o, s = self.forward_propagation(x)
    # We accumulate the gradients in these variables
    dLdU = np.zeros(self.U.shape)
    dLdV = np.zeros(self.V.shape)
    dLdW = np.zeros(self.W.shape)
    delta_o = o
    delta_o[np.arange(len(y)), y] -= 1.
    for t in np.arange(T)[::-1]:
        dLdV += np.outer(delta_o[t], s[t].T)
        # Initial delta calculation
        delta_t = self.V.T.dot(delta_o[t]) * (1 - (s[t] ** 2))
        # Backpropagation through time (for at most self.bptt_truncate)
        for bptt_step in np.arange(max(0, t-self.bptt_truncate), t+1)[::-1]:
            #print "backpropagation step t=%d bptt step=%d " % (t, bptt_step)
            dLdW += np.outer(delta_t, s[bptt_step-1])
            dLdU[:, x[bptt_step]] += delta_t
            # update delta for next step
            delta_t = self.W.T.dot(delta_t) * (1 - s[bptt_step-1] ** 2)
    return [dLdU, dLdV, dLdW]
RNNNumpy.bptt = bptt        

In [15]:
def gradient_check(self, x, y, h=0.001, error_threshold=0.01):
    # calculate the gradients using backpropagation.
    bptt_gradients = model.bptt(x, y)
    # list of all paramerts we want to check
    model_parameters = ['U', 'V', 'W']
    # gradient check for each parameter
    for pidx, pname in enumerate(model_parameters):
        # get the actual parameter value from the mode
        parameter = operator.attrgetter(pname)(self)
        print "Performing gradient check for parameter %s with size %d." % (pname, np.prod(parameter.shape))
        # iterate over each element of the parameter matrix, eg. (0,0), (0,1)
        it = np.nditer(parameter, flags=['multi_index'], op_flags=['readwrite'])
        while not it.finished:
            ix = it.multi_index
            # save the original value so we can reset it later
            original_value = parameter[ix]
            # estimate the gradient using (f(x+h) - f(x-h) / (2*h))
            parameter[ix] = original_value + h
            gradplus = model.calculate_total_loss([x], [y])
            parameter[ix] = original_value - h
            gradminus = model.calculate_total_loss([x], [y])
            estimated_gradient = (gradplus - gradminus) / (2*h)
            # reset parameter to original value
            parameter[ix] = original_value
            # the gradient for this parameter calculated using backpropagation
            backprop_gradient = bptt_gradients[pidx][ix]
            # calculate the relative error: ([x - y] / (|x| + |y|))
            relative_error = np.abs(backprop_gradient - estimated_gradient) / (np.abs(backprop_gradient) + np.abs(estimated_gradient))
            # if the error is to large fail the gradient check
            if relative_error > error_threshold:
                print "gradient check error: parameter=%s ix=%s" % (pname, ix)
                print "+h Loss: %f" % gradplus
                print "-h Loss: %f" % gradminus
                print "estimated_gradient: %f" % estimated_gradient
                print "backpropagation gradient: %f" % backprop_gradient
                print "relative error: %f" % relative_error
                return
            it.iternext()
        print "gradient check for parameter %s passed." % (pname)
    
RNNNumpy.gradient_check = gradient_check

# to avoid performing millions of expensive calculation we use a smaller vocabulary size for checking
gradient_check_vocab_size = 100
np.random.seed(10)
model = RNNNumpy(gradient_check_vocab_size, 10, bptt_truncate=1000)
model.gradient_check([0, 1, 2, 3], [1, 2, 3, 4])


backpropagation step t=3 bptt step=3 
backpropagation step t=3 bptt step=2 
backpropagation step t=3 bptt step=1 
backpropagation step t=3 bptt step=0 
backpropagation step t=2 bptt step=2 
backpropagation step t=2 bptt step=1 
backpropagation step t=2 bptt step=0 
backpropagation step t=1 bptt step=1 
backpropagation step t=1 bptt step=0 
backpropagation step t=0 bptt step=0 
Performing gradient check for parameter U with size 1000.


/home/jameschien/anaconda2/lib/python2.7/site-packages/ipykernel_launcher.py:28: RuntimeWarning: invalid value encountered in double_scalars


gradient check for parameter U passed.
Performing gradient check for parameter V with size 1000.
gradient check for parameter V passed.
Performing gradient check for parameter W with size 100.
gradient check for parameter W passed.


In [16]:
def numpy_sgd_step(self, x, y, learning_rate):
    # calculate the gradients
    dLdU, dLdV, dLdW = self.bptt(x, y)
    # change parameters according to gradients and learning rate
    self.U -= learning_rate * dLdU
    self.V -= learning_rate * dLdV
    self.W -= learning_rate * dLdW

RNNNumpy.sgd_step = numpy_sgd_step

In [17]:
# outer SGD loop
# - model: The RNN model instance
# - X_train: The training data set
# - y_train: The training data labels
# - learning_rate: Initial learning rate for SGD
# - nepoch: Number of times to iterate through the complete dataset
# - evaluate_loss_after: Evaluate the loss after this many epochs
def train_with_sgd(model, x_train, y_train, learning_rate=0.005, nepoch=100, evaluate_loss_after=5):
    # we keep track of the losses so we can plot them later
    losses = []
    num_examples_seen = 0
    for epoch in range(nepoch):
        # optinally evaluate the loss
        if (epoch % evaluate_loss_after == 0):
            loss = model.calculate_loss(X_train, y_train)
            losses.append((num_examples_seen, loss))
            time = datetime.now().strftime('%Y-%m-%d %H:%M:%S')
            print "%s: Loss after num_examples_seen=%d epoch=%d: %f" % (time, num_examples_seen, epoch, loss)
            
            # adjust the learning rate if loss increases
            if (len(losses) > 1 and losses[-1][1] > losses[-2][1]):
                learning_rate = learning_rate * 0.5
                print "setting learning rate to %f" % learning_rate
                sys.stdout.flush()
        # for each training example
        for i in range(len(y_train)):
            # one sgd step
            model.sgd_step(X_train[i], y_train[i], learning_rate)
            num_examples_seen += 1

In [18]:
np.random.seed(10)
# train on a small subset of the data to see what happens
model = RNNNumpy(vocabulary_size)
losses = train_with_sgd(model, X_train[:100], y_train[:100], nepoch=10, evaluate_loss_after=1)

2017-08-07 09:34:51: Loss after num_examples_seen=0 epoch=0: 8.987468
backpropagation step t=19 bptt step=19 
backpropagation step t=19 bptt step=18 
backpropagation step t=19 bptt step=17 
backpropagation step t=19 bptt step=16 
backpropagation step t=19 bptt step=15 
backpropagation step t=18 bptt step=18 
backpropagation step t=18 bptt step=17 
backpropagation step t=18 bptt step=16 
backpropagation step t=18 bptt step=15 
backpropagation step t=18 bptt step=14 
backpropagation step t=17 bptt step=17 
backpropagation step t=17 bptt step=16 
backpropagation step t=17 bptt step=15 
backpropagation step t=17 bptt step=14 
backpropagation step t=17 bptt step=13 
backpropagation step t=16 bptt step=16 
backpropagation step t=16 bptt step=15 
backpropagation step t=16 bptt step=14 
backpropagation step t=16 bptt step=13 
backpropagation step t=16 bptt step=12 
backpropagation step t=15 bptt step=15 
backpropagation step t=15 bptt step=14 
backpropagation step t=15 bptt step=13 
backpropag

backpropagation step t=23 bptt step=23 
backpropagation step t=23 bptt step=22 
backpropagation step t=23 bptt step=21 
backpropagation step t=23 bptt step=20 
backpropagation step t=23 bptt step=19 
backpropagation step t=22 bptt step=22 
backpropagation step t=22 bptt step=21 
backpropagation step t=22 bptt step=20 
backpropagation step t=22 bptt step=19 
backpropagation step t=22 bptt step=18 
backpropagation step t=21 bptt step=21 
backpropagation step t=21 bptt step=20 
backpropagation step t=21 bptt step=19 
backpropagation step t=21 bptt step=18 
backpropagation step t=21 bptt step=17 
backpropagation step t=20 bptt step=20 
backpropagation step t=20 bptt step=19 
backpropagation step t=20 bptt step=18 
backpropagation step t=20 bptt step=17 
backpropagation step t=20 bptt step=16 
backpropagation step t=19 bptt step=19 
backpropagation step t=19 bptt step=18 
backpropagation step t=19 bptt step=17 
backpropagation step t=19 bptt step=16 
backpropagation step t=19 bptt step=15 


backpropagation step t=13 bptt step=13 
backpropagation step t=13 bptt step=12 
backpropagation step t=13 bptt step=11 
backpropagation step t=13 bptt step=10 
backpropagation step t=13 bptt step=9 
backpropagation step t=12 bptt step=12 
backpropagation step t=12 bptt step=11 
backpropagation step t=12 bptt step=10 
backpropagation step t=12 bptt step=9 
backpropagation step t=12 bptt step=8 
backpropagation step t=11 bptt step=11 
backpropagation step t=11 bptt step=10 
backpropagation step t=11 bptt step=9 
backpropagation step t=11 bptt step=8 
backpropagation step t=11 bptt step=7 
backpropagation step t=10 bptt step=10 
backpropagation step t=10 bptt step=9 
backpropagation step t=10 bptt step=8 
backpropagation step t=10 bptt step=7 
backpropagation step t=10 bptt step=6 
backpropagation step t=9 bptt step=9 
backpropagation step t=9 bptt step=8 
backpropagation step t=9 bptt step=7 
backpropagation step t=9 bptt step=6 
backpropagation step t=9 bptt step=5 
backpropagation step

backpropagation step t=7 bptt step=7 
backpropagation step t=7 bptt step=6 
backpropagation step t=7 bptt step=5 
backpropagation step t=7 bptt step=4 
backpropagation step t=7 bptt step=3 
backpropagation step t=6 bptt step=6 
backpropagation step t=6 bptt step=5 
backpropagation step t=6 bptt step=4 
backpropagation step t=6 bptt step=3 
backpropagation step t=6 bptt step=2 
backpropagation step t=5 bptt step=5 
backpropagation step t=5 bptt step=4 
backpropagation step t=5 bptt step=3 
backpropagation step t=5 bptt step=2 
backpropagation step t=5 bptt step=1 
backpropagation step t=4 bptt step=4 
backpropagation step t=4 bptt step=3 
backpropagation step t=4 bptt step=2 
backpropagation step t=4 bptt step=1 
backpropagation step t=4 bptt step=0 
backpropagation step t=3 bptt step=3 
backpropagation step t=3 bptt step=2 
backpropagation step t=3 bptt step=1 
backpropagation step t=3 bptt step=0 
backpropagation step t=2 bptt step=2 
backpropagation step t=2 bptt step=1 
backpropagat

backpropagation step t=7 bptt step=7 
backpropagation step t=7 bptt step=6 
backpropagation step t=7 bptt step=5 
backpropagation step t=7 bptt step=4 
backpropagation step t=7 bptt step=3 
backpropagation step t=6 bptt step=6 
backpropagation step t=6 bptt step=5 
backpropagation step t=6 bptt step=4 
backpropagation step t=6 bptt step=3 
backpropagation step t=6 bptt step=2 
backpropagation step t=5 bptt step=5 
backpropagation step t=5 bptt step=4 
backpropagation step t=5 bptt step=3 
backpropagation step t=5 bptt step=2 
backpropagation step t=5 bptt step=1 
backpropagation step t=4 bptt step=4 
backpropagation step t=4 bptt step=3 
backpropagation step t=4 bptt step=2 
backpropagation step t=4 bptt step=1 
backpropagation step t=4 bptt step=0 
backpropagation step t=3 bptt step=3 
backpropagation step t=3 bptt step=2 
backpropagation step t=3 bptt step=1 
backpropagation step t=3 bptt step=0 
backpropagation step t=2 bptt step=2 
backpropagation step t=2 bptt step=1 
backpropagat

...

backpropagation step t=17 bptt step=17 
backpropagation step t=17 bptt step=16 
backpropagation step t=17 bptt step=15 
backpropagation step t=17 bptt step=14 
backpropagation step t=17 bptt step=13 
backpropagation step t=16 bptt step=16 
backpropagation step t=16 bptt step=15 
backpropagation step t=16 bptt step=14 
backpropagation step t=16 bptt step=13 
backpropagation step t=16 bptt step=12 
backpropagation step t=15 bptt step=15 
backpropagation step t=15 bptt step=14 
backpropagation step t=15 bptt step=13 
backpropagation step t=15 bptt step=12 
backpropagation step t=15 bptt step=11 
backpropagation step t=14 bptt step=14 
backpropagation step t=14 bptt step=13 
backpropagation step t=14 bptt step=12 
backpropagation step t=14 bptt step=11 
backpropagation step t=14 bptt step=10 
backpropagation step t=13 bptt step=13 
backpropagation step t=13 bptt step=12 
backpropagation step t=13 bptt step=11 
backpropagation step t=13 bptt step=10 
backpropagation step t=13 bptt step=9 
b

backpropagation step t=1 bptt step=1 
backpropagation step t=1 bptt step=0 
backpropagation step t=0 bptt step=0 
backpropagation step t=16 bptt step=16 
backpropagation step t=16 bptt step=15 
backpropagation step t=16 bptt step=14 
backpropagation step t=16 bptt step=13 
backpropagation step t=16 bptt step=12 
backpropagation step t=15 bptt step=15 
backpropagation step t=15 bptt step=14 
backpropagation step t=15 bptt step=13 
backpropagation step t=15 bptt step=12 
backpropagation step t=15 bptt step=11 
backpropagation step t=14 bptt step=14 
backpropagation step t=14 bptt step=13 
backpropagation step t=14 bptt step=12 
backpropagation step t=14 bptt step=11 
backpropagation step t=14 bptt step=10 
backpropagation step t=13 bptt step=13 
backpropagation step t=13 bptt step=12 
backpropagation step t=13 bptt step=11 
backpropagation step t=13 bptt step=10 
backpropagation step t=13 bptt step=9 
backpropagation step t=12 bptt step=12 
backpropagation step t=12 bptt step=11 
backpro

backpropagation step t=35 bptt step=35 
backpropagation step t=35 bptt step=34 
backpropagation step t=35 bptt step=33 
backpropagation step t=35 bptt step=32 
backpropagation step t=35 bptt step=31 
backpropagation step t=34 bptt step=34 
backpropagation step t=34 bptt step=33 
backpropagation step t=34 bptt step=32 
backpropagation step t=34 bptt step=31 
backpropagation step t=34 bptt step=30 
backpropagation step t=33 bptt step=33 
backpropagation step t=33 bptt step=32 
backpropagation step t=33 bptt step=31 
backpropagation step t=33 bptt step=30 
backpropagation step t=33 bptt step=29 
backpropagation step t=32 bptt step=32 
backpropagation step t=32 bptt step=31 
backpropagation step t=32 bptt step=30 
backpropagation step t=32 bptt step=29 
backpropagation step t=32 bptt step=28 
backpropagation step t=31 bptt step=31 
backpropagation step t=31 bptt step=30 
backpropagation step t=31 bptt step=29 
backpropagation step t=31 bptt step=28 
backpropagation step t=31 bptt step=27 


backpropagation step t=11 bptt step=11 
backpropagation step t=11 bptt step=10 
backpropagation step t=11 bptt step=9 
backpropagation step t=11 bptt step=8 
backpropagation step t=11 bptt step=7 
backpropagation step t=10 bptt step=10 
backpropagation step t=10 bptt step=9 
backpropagation step t=10 bptt step=8 
backpropagation step t=10 bptt step=7 
backpropagation step t=10 bptt step=6 
backpropagation step t=9 bptt step=9 
backpropagation step t=9 bptt step=8 
backpropagation step t=9 bptt step=7 
backpropagation step t=9 bptt step=6 
backpropagation step t=9 bptt step=5 
backpropagation step t=8 bptt step=8 
backpropagation step t=8 bptt step=7 
backpropagation step t=8 bptt step=6 
backpropagation step t=8 bptt step=5 
backpropagation step t=8 bptt step=4 
backpropagation step t=7 bptt step=7 
backpropagation step t=7 bptt step=6 
backpropagation step t=7 bptt step=5 
backpropagation step t=7 bptt step=4 
backpropagation step t=7 bptt step=3 
backpropagation step t=6 bptt step=6 

backpropagation step t=4 bptt step=4 
backpropagation step t=4 bptt step=3 
backpropagation step t=4 bptt step=2 
backpropagation step t=4 bptt step=1 
backpropagation step t=4 bptt step=0 
backpropagation step t=3 bptt step=3 
backpropagation step t=3 bptt step=2 
backpropagation step t=3 bptt step=1 
backpropagation step t=3 bptt step=0 
backpropagation step t=2 bptt step=2 
backpropagation step t=2 bptt step=1 
backpropagation step t=2 bptt step=0 
backpropagation step t=1 bptt step=1 
backpropagation step t=1 bptt step=0 
backpropagation step t=0 bptt step=0 
backpropagation step t=9 bptt step=9 
backpropagation step t=9 bptt step=8 
backpropagation step t=9 bptt step=7 
backpropagation step t=9 bptt step=6 
backpropagation step t=9 bptt step=5 
backpropagation step t=8 bptt step=8 
backpropagation step t=8 bptt step=7 
backpropagation step t=8 bptt step=6 
backpropagation step t=8 bptt step=5 
backpropagation step t=8 bptt step=4 
backpropagation step t=7 bptt step=7 
backpropagat

In [25]:
def generate_sentence(model):
    # we start the sentence with the start token
    new_sentence = [word_to_index[sentence_start_token]]
    # repeat until we get an end token
    while not new_sentence[-1] == word_to_index[sentence_end_token]:
        next_word_probs, _ = model.forward_propagation(new_sentence)
        sampled_word = word_to_index[unknown_token]
        # we don't want to sample unknown words
        while sampled_word == word_to_index[unknown_token]:
            samples = np.random.multinomial(1, next_word_probs[-1])
            sampled_word = np.argmax(samples)
        new_sentence.append(sampled_word)
    sentence_str = [index_to_word[x] for x in new_sentence[1:-1]]
    return sentence_str

In [29]:
num_sentence = 10
sentence_min_length = 7

for i in range(num_sentence):
    sent = []
    # we want long sentences, not sentences with one or two words
    while len(sent) < sentence_min_length:
        sent = generate_sentence(model)
    print " ".join(sent)

bud application so were the elder 's door a suddenly a for on of ( used on for genres and the sellers ) who new to .
walks that the basically , the class but the contact is professor type it the the the london whichever '' intent common but '' change rejected , a somewhere the ) notable .
is less walls excuse vocal consequence the ! the back and the event physics the west s idle ashamed having is he bad negative having a to wo the wired be the to guardian sound ; just what made the like are technologies nature non the go the door dutch it junk . and the jackson is ( that ) your kicking cooler ? the and of is always advocate it squad the the son the for ppr ; , neck unsure have perceived true and currently the pot auto 's me the prison has concerned them refuse . dumb send and the house that the never protest trauma installed
demonstrate an have same '' if for not emotional wondered the going & my have ham la n't the a .
account that jersey lands her but a n't .
fellow other and and sil